In [1]:
import datarobot as dr
import pandas as pd
import numpy as np
import datetime as dt

In [16]:
import datarobot_ts_helpers as dr_helpers

In [2]:
import os
import re 
from importlib import reload
from ts_metrics import *
from ts_pre_processing import *
from ts_calendar import *
from ts_projects import *
from ts_modeling import *
from ts_clustering import *
from ts_data_quality import *
from ts_predictions import *

In [5]:
pd.set_option('display.max_colwidth', -1)

/Users/belen.sanchez/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  """Entry point for launching an IPython kernel.


In [6]:
pd.set_option('display.max_rows', None)

In [7]:
# Connect to DRClient
dr.Client(config_path = './drconfig.yaml')

# Load Data

In [36]:
# import dataset
training = pd.read_csv('./cognex_data_region_latest.csv')
training.shape

(70004, 15)

# Create date feature

In [37]:
def create_series(df, cols_to_concat, convert=True):
    df = df[cols_to_concat].copy()
    non_strings = [c for c in df[cols_to_concat] if df[c].dtype != 'object']

    if len(non_strings) > 0:
        if convert:
            df[non_strings] = df[non_strings].applymap(str)
        else:
            raise TypeError("columns must all be type str")

    df['series_id'] = df[cols_to_concat].apply(lambda x: '/'.join(x), axis=1)
    return df['series_id']

In [38]:
# Create a date column by concatenating year and month and adding 1st day of month

In [39]:
cols_to_concat = ['year', 'fiscal_period']
new_series = create_series(training, cols_to_concat, convert = True)
training['date'] = new_series
training.head(3)


year  fiscal_period      Area         region industry1  \
0  2017  12             Americas  Americas West  Other      
1  2017  12             Americas  Americas West  Other      
2  2017  12             Americas  Americas West  Other      

  account classification     product  nb of appointments  \
0  Non-Strategic          INS FACTRY  0                    
1  Non-Strategic          INS SENSOR  0                    
2  Non-Strategic          DATAMAN     0                    

   nb of technical request  nb of opportunities created  \
0  0                        0                             
1  0                        0                             
2  0                        0                             

   nb of opportunities qualified  nb of opportunities forecasted  \
0  0                              0                                
1  0                              0                                
2  0                              0                                

   weighed funnel values  opportunities average nb of months  booking value  \
0  0                      0.0                                 410             
1  0                      0.0                                 0               
2  0                      0.0                                 1121            

      date  
0  2017/12  
1  2017/12  
2  2017/12

In [40]:
training.Area.unique()

array(['Americas', 'Europe', 'GTR China', 'Japan', 'KIA'], dtype=object)

In [41]:
training['date'] = training['date'].astype(str)+'/01'
training.head(3)

year  fiscal_period      Area         region industry1  \
0  2017  12             Americas  Americas West  Other      
1  2017  12             Americas  Americas West  Other      
2  2017  12             Americas  Americas West  Other      

  account classification     product  nb of appointments  \
0  Non-Strategic          INS FACTRY  0                    
1  Non-Strategic          INS SENSOR  0                    
2  Non-Strategic          DATAMAN     0                    

   nb of technical request  nb of opportunities created  \
0  0                        0                             
1  0                        0                             
2  0                        0                             

   nb of opportunities qualified  nb of opportunities forecasted  \
0  0                              0                                
1  0                              0                                
2  0                              0                                

   weighed funnel values  opportunities average nb of months  booking value  \
0  0                      0.0                                 410             
1  0                      0.0                                 0               
2  0                      0.0                                 1121            

         date  
0  2017/12/01  
1  2017/12/01  
2  2017/12/01

In [42]:
# comvert date to datetime format
training['date']= pd.to_datetime(training['date'])

# Create new series id

In [43]:
# create series id concatenating Area and Product
cols_to_concat = ['Area', 'product']
new_series = dr_helpers.create_series_id(training, cols_to_concat, convert = True)
training['Area_product'] = new_series
training.head(3)

year  fiscal_period      Area         region industry1  \
0  2017  12             Americas  Americas West  Other      
1  2017  12             Americas  Americas West  Other      
2  2017  12             Americas  Americas West  Other      

  account classification     product  nb of appointments  \
0  Non-Strategic          INS FACTRY  0                    
1  Non-Strategic          INS SENSOR  0                    
2  Non-Strategic          DATAMAN     0                    

   nb of technical request  nb of opportunities created  \
0  0                        0                             
1  0                        0                             
2  0                        0                             

   nb of opportunities qualified  nb of opportunities forecasted  \
0  0                              0                                
1  0                              0                                
2  0                              0                                

   weighed funnel values  opportunities average nb of months  booking value  \
0  0                      0.0                                 410             
1  0                      0.0                                 0               
2  0                      0.0                                 1121            

        date         Area_product  
0 2017-12-01  Americas_INS FACTRY  
1 2017-12-01  Americas_INS SENSOR  
2 2017-12-01  Americas_DATAMAN

In [44]:
# sort values 
training.sort_values(['Area_product', 'date'], ascending=[True, True], inplace=True)
training.head()

year  fiscal_period      Area            region   industry1  \
20  2017  12             Americas  Other             Automotive   
27  2017  12             Americas  Americas Central  Automotive   
41  2017  12             Americas  Americas LATAM    Automotive   
49  2017  12             Americas  Americas South    Automotive   
68  2017  12             Americas  Americas East     Automotive   

   account classification product  nb of appointments  \
20  Non-Strategic          3D      0                    
27  Non-Strategic          3D      0                    
41  Non-Strategic          3D      0                    
49  Non-Strategic          3D      0                    
68  Strategic              3D      0                    

    nb of technical request  nb of opportunities created  \
20  0                        2                             
27  0                        3                             
41  0                        3                             
49  0                        1                             
68  0                        0                             

    nb of opportunities qualified  nb of opportunities forecasted  \
20  2                              0                                
27  3                              0                                
41  3                              0                                
49  1                              0                                
68  0                              0                                

    weighed funnel values  opportunities average nb of months  booking value  \
20  0                      0.0                                 0               
27  0                      0.0                                 33              
41  0                      0.0                                 442             
49  0                      0.0                                 0               
68  0                      0.0                                 98870           

         date Area_product  
20 2017-12-01  Americas_3D  
27 2017-12-01  Americas_3D  
41 2017-12-01  Americas_3D  
49 2017-12-01  Americas_3D  
68 2017-12-01  Americas_3D

In [45]:
training.columns

Index(['year', 'fiscal_period', 'Area', 'region', 'industry1',
       'account classification', 'product', 'nb of appointments',
       'nb of technical request', 'nb of opportunities created',
       'nb of opportunities qualified', 'nb of opportunities forecasted',
       'weighed funnel values', 'opportunities average nb of months',
       'booking value', 'date', 'Area_product'],
      dtype='object')

# Set up project

In [46]:
#Set all values here.
#One important point, if you decide to change to monthly or weekly ts_settings should be 
#Changed afterwards, as weekly and monthly dates are based on the original date_col

today = pd.to_datetime("today")
target = 'booking value'
date_col = 'date'
kia = ['nb of opportunities forecasted', 'weighed funnel values', 'opportunities average nb of months']
series_id = 'Area_product'
pj_name = series_id + "_Project"+"_"+str(today)[0:10]
fd_start = 1
fd_end = 1
fdw_start = -3
fdw_end = 0
num_backtests = 2
#calendar =dr.CalendarFile.create("canada_calendar.csv")
# Create TS Settings
ts_settings = {'use_time_series':training,'project_name':pj_name, 'known_in_advance':kia,
               'series_id':series_id,  'target':target, 'date_col':date_col,'num_backtests':num_backtests,
               'fd_start':fd_start, 'fd_end':fd_end, 'fdw_start':fdw_start, 'fdw_end':fdw_end
               }


#Add a week date, and a month date 
training['week_number'] = training[ts_settings['date_col']].map(lambda x: x.strftime("%W"))
training['month_date'] = training[ts_settings['date_col']].map(lambda x: str(x)[0:7]+"-01")
training = training.sort_values(by=ts_settings['date_col'], ascending=False)

In [47]:
training.head()

year  fiscal_period      Area            region      industry1  \
69995  2020  7              KIA       KIA-KOREA         Semiconductor   
70000  2020  7              KIA       KIA-INDIA         Semiconductor   
68149  2020  7              Americas  Americas Central  Packaging       
68154  2020  7              Americas  Americas East     Packaging       
68159  2020  7              Americas  Americas LATAM    Packaging       

      account classification     product  nb of appointments  \
69995  Strategic Existing     WAFER ID    0                    
70000  White Space            INS FACTRY  0                    
68149  White Space            INS FACTRY  0                    
68154  White Space            INS FACTRY  0                    
68159  White Space            INS FACTRY  0                    

       nb of technical request  nb of opportunities created  \
69995  0                        2                             
70000  1                        2                             
68149  1                        3                             
68154  0                        3                             
68159  1                        6                             

       nb of opportunities qualified  nb of opportunities forecasted  \
69995  2                              0                                
70000  0                              0                                
68149  2                              0                                
68154  0                              3                                
68159  2                              0                                

       weighed funnel values  opportunities average nb of months  \
69995  0                      0.0                                  
70000  0                      0.0                                  
68149  20000                  0.0                                  
68154  28030                  1.0                                  
68159  0                      0.0                                  

       booking value       date         Area_product week_number  month_date  
69995  0             2020-07-01  KIA_WAFER ID         26          2020-07-01  
70000  0             2020-07-01  KIA_INS FACTRY       26          2020-07-01  
68149  23397         2020-07-01  Americas_INS FACTRY  26          2020-07-01  
68154  40859         2020-07-01  Americas_INS FACTRY  26          2020-07-01  
68159 -5055          2020-07-01  Americas_INS FACTRY  26          2020-07-01

# Supporting Functions

In [48]:
#Function to concatenate strings or integers into one string
def concate_unique_strings (val):
    tmp = ""
    val = set(val)
    val = list(val)
    for i in val:
        s = str(i).strip()
        tmp = tmp + ', '+ s
    tmp = tmp[2:]
    return (tmp)
#Create a data frame with series_id and series_date where series dates are continuous and 
#don't have gaps. This dataframe has not only continuous dates for each series_id, but also
#has month_date, and week_date in case one wants to aggregate by week or day
def  create_continuous_dates_df(data_df,series_id,series_date):
    '''data_df: dataframe
       series_id: the multi-series id in this case it can be Area, region, product or Area_product
       Create a dateframe with series_id and series_date'''
    product_dates = training.groupby(ts_settings["series_id"])[ts_settings["date_col"]].agg(['min', 'max'])
    product_dates = product_dates.reset_index()
    product_dates.rename(columns={'min':'Date_Min','max':'Date_Max'}, inplace=True)
    n_rows =product_dates.shape[0]
    invoice_df = pd.DataFrame()
    for i in range(n_rows):
        dates2add = pd.date_range(product_dates.iloc[i,:].Date_Min, product_dates.iloc[i,:].Date_Max).tolist()
        tmp_df = pd.DataFrame({series_id : product_dates.iloc[i,:][ts_settings["series_id"]],series_date : dates2add})
        invoice_df = invoice_df.append(tmp_df,ignore_index=True)
    invoice_df['years'] = invoice_df[ts_settings['date_col']].map( lambda x: str(x)[0:4])
    invoice_df['week_number'] = invoice_df[ts_settings['date_col']].map(lambda x: x.strftime("%W"))
    invoice_df = invoice_df.sort_values(by=ts_settings['date_col'], ascending=False)
    invoice_df['week_date'] = invoice_df.groupby(['years','week_number'])[ts_settings['date_col']].transform('min')
    invoice_df['month_date'] = invoice_df[ts_settings['date_col']].map(lambda x: str(x)[0:7]+"-01")
    
    return(invoice_df)



In [49]:
def group_by_area_product(data_df,series_id,data_col):
    '''data_df:  original dataframe (training)
       series_id: multi time-series group
       date_col : the date used by time-series
       This is just an example, on how one can combine categorical features.  I decided to 
       combine some, and just count the number of unique values for others'''
    
    products_df =  data_df.groupby([series_id,data_col]).agg(
        Area_Txt = ("Area",lambda x: concate_unique_strings(x)),
        region_Txt = ("region",lambda x: concate_unique_strings(x)),
        industry1_Txt = ("industry1",lambda x: concate_unique_strings(x)),
        account_class_Txt = ("account classification",lambda x: concate_unique_strings(x)),
        product_Txt = ("product",lambda x: concate_unique_strings(x))
    )
  
    tmp_agg = training.groupby([series_id,data_col]).agg({
       "Area" : ["nunique"], 
       "region" : ["nunique"],
       "industry1" : ["nunique"], 
       "account classification" : ["nunique"],
       "product" : ["nunique"],
       "booking value" :["sum"],
       "nb of appointments" :["sum"],
       "nb of technical request": ["sum"],
       "nb of opportunities created": ["sum"],
       "nb of opportunities forecasted": ["sum"],
       "nb of opportunities qualified": ["sum"],
       "weighed funnel values": ["sum"],
       "opportunities average nb of months": ["sum"]
    })
    tmp_agg.columns = ["_".join(x) for x in tmp_agg.columns.ravel()]
    products_final = pd.merge(left=products_df, right=tmp_agg, 
                          left_on=[series_id,data_col], 
                          right_on=[series_id,data_col],
                          how = "inner")
    products_final = products_final.reset_index()
    return(products_final)

In [50]:
group_map = {"Area_product": group_by_area_product}

In [51]:

#Prepare the dataframe for DataRobot
def make_dataset(date_df,data_df):
    '''data_df: in here will be the original dataset training
    This function just combine all the other functions written above to create 
    the final dataframe that will be used for training'''
    date_df.loc[:,[ts_settings['series_id'],ts_settings['date_col']]].drop_duplicates( keep = 'first', inplace = True)
    tmp_df = pd.merge(left=date_df, right=data_df, 
                          left_on=[ts_settings['series_id'],ts_settings['date_col']], 
                          right_on=[ts_settings['series_id'],ts_settings['date_col']],
                          how = "left")
    action = group_map[ts_settings["series_id"]]
    final_df = action(tmp_df,ts_settings['series_id'],ts_settings['date_col'])
    final_df.rename(columns={ts_settings['target']+"_sum":ts_settings['target']}, inplace=True)
    features_2_set_2_zero = list(final_df.select_dtypes(include=[np.number]).columns.values)
    final_df.loc[:,features_2_set_2_zero] = final_df.loc[:,features_2_set_2_zero].fillna(0)
    tmp_df = date_df.loc[:,[ts_settings['series_id'],ts_settings['date_col']]].copy()
    tmp_df.drop_duplicates(keep = 'first', inplace = True)
    final_df = pd.merge(left=tmp_df, right=final_df, 
                          left_on=[ts_settings['series_id'],ts_settings['date_col']], 
                          right_on=[ts_settings['series_id'],ts_settings['date_col']],
                          how = "left")
    features_2_set_2_zero = list(final_df.select_dtypes(include=[np.number]).columns.values)
    final_df.loc[:,features_2_set_2_zero] = final_df.loc[:,features_2_set_2_zero].fillna(0) 
    final_df[ts_settings['date_col']]= pd.to_datetime(final_df[ts_settings['date_col']]) 
    return(final_df)



In [52]:
#Aggregate by BRP_Model_Group
def prepare_data():
    ts_settings['date_col'] = "month_date"
    date_df =  create_continuous_dates_df(ts_settings['use_time_series'],
                                          ts_settings['series_id'],ts_settings['date_col'])
    final_df = make_dataset(date_df,training) 
    return (final_df)

In [53]:
final_df = prepare_data()
ts_settings['use_time_series'] = final_df

In [54]:
final_df.sort_values(by=[ts_settings['series_id'],ts_settings['date_col']])

Area_product month_date   Area_Txt  \
2047  Americas_3D             2017-12-01  Americas    
1999  Americas_3D             2018-01-01  Americas    
1924  Americas_3D             2018-02-01  Americas    
1831  Americas_3D             2018-03-01  Americas    
1779  Americas_3D             2018-04-01  Americas    
1734  Americas_3D             2018-05-01  Americas    
1689  Americas_3D             2018-06-01  Americas    
1564  Americas_3D             2018-07-01  Americas    
1523  Americas_3D             2018-08-01  Americas    
1495  Americas_3D             2018-09-01  Americas    
1428  Americas_3D             2018-10-01  Americas    
1358  Americas_3D             2018-11-01  Americas    
1273  Americas_3D             2018-12-01  Americas    
1202  Americas_3D             2019-01-01  Americas    
1153  Americas_3D             2019-02-01  Americas    
1089  Americas_3D             2019-03-01  Americas    
975   Americas_3D             2019-04-01  Americas    
904   Americas_3D             2019-05-01  Americas    
850   Americas_3D             2019-06-01  Americas    
830   Americas_3D             2019-07-01  Americas    
765   Americas_3D             2019-08-01  Americas    
667   Americas_3D             2019-09-01  Americas    
631   Americas_3D             2019-10-01  Americas    
558   Americas_3D             2019-11-01  Americas    
483   Americas_3D             2019-12-01  Americas    
397   Americas_3D             2020-01-01  Americas    
340   Americas_3D             2020-02-01  Americas    
290   Americas_3D             2020-03-01  Americas    
222   Americas_3D             2020-04-01  Americas    
128   Americas_3D             2020-05-01  Americas    
113   Americas_3D             2020-06-01  Americas    
4     Americas_3D             2020-07-01  Americas    
2066  Americas_3D SENSOR      2017-12-01  Americas    
2000  Americas_3D SENSOR      2018-01-01  Americas    
1909  Americas_3D SENSOR      2018-02-01  Americas    
1825  Americas_3D SENSOR      2018-03-01  Americas    
1771  Americas_3D SENSOR      2018-04-01  Americas    
1720  Americas_3D SENSOR      2018-05-01  Americas    
1641  Americas_3D SENSOR      2018-06-01  Americas    
1565  Americas_3D SENSOR      2018-07-01  Americas    
1549  Americas_3D SENSOR      2018-08-01  Americas    
1443  Americas_3D SENSOR      2018-09-01  Americas    
1418  Americas_3D SENSOR      2018-10-01  Americas    
1305  Americas_3D SENSOR      2018-11-01  Americas    
1253  Americas_3D SENSOR      2018-12-01  Americas    
1169  Americas_3D SENSOR      2019-01-01  Americas    
1114  Americas_3D SENSOR      2019-02-01  Americas    
1043  Americas_3D SENSOR      2019-03-01  Americas    
974   Americas_3D SENSOR      2019-04-01  Americas    
941   Americas_3D SENSOR      2019-05-01  Americas    
838   Americas_3D SENSOR      2019-06-01  Americas    
829   Americas_3D SENSOR      2019-07-01  Americas    
767   Americas_3D SENSOR      2019-08-01  Americas    
650   Americas_3D SENSOR      2019-09-01  Americas    
633   Americas_3D SENSOR      2019-10-01  Americas    
556   Americas_3D SENSOR      2019-11-01  Americas    
502   Americas_3D SENSOR      2019-12-01  Americas    
424   Americas_3D SENSOR      2020-01-01  Americas    
376   Americas_3D SENSOR      2020-02-01  Americas    
316   Americas_3D SENSOR      2020-03-01  Americas    
235   Americas_3D SENSOR      2020-04-01  Americas    
180   Americas_3D SENSOR      2020-05-01  Americas    
69    Americas_3D SENSOR      2020-06-01  Americas    
53    Americas_3D SENSOR      2020-07-01  Americas    
2069  Americas_ADV ENGINE     2017-12-01  Americas    
1957  Americas_ADV ENGINE     2018-01-01  Americas    
1895  Americas_ADV ENGINE     2018-02-01  Americas    
1874  Americas_ADV ENGINE     2018-03-01  Americas    
1812  Americas_ADV ENGINE     2018-04-01  Americas    
1740  Americas_ADV ENGINE     2018-05-01  Americas    
1671  Americas_ADV ENGINE     2018-06-01  NaN         
1618  Americas_ADV ENGINE     2018-07-01  Americas    
15

In [55]:
final_df.reset_index(drop=True)

Area_product month_date   Area_Txt  \
0     KIA_WAFER ID            2020-07-01  KIA         
1     GTR China_DATAMAN       2020-07-01  GTR China   
2     GTR China_3D SENSOR     2020-07-01  GTR China   
3     GTR China_ADV ENGINE    2020-07-01  GTR China   
4     Americas_3D             2020-07-01  Americas    
5     GTR China_CHECKER       2020-07-01  GTR China   
6     Americas_WAFER ID       2020-07-01  Americas    
7     Americas_DATAMAN        2020-07-01  Americas    
8     Europe_ADV ENGINE       2020-07-01  Europe      
9     KIA_DEEP LEARNING       2020-07-01  KIA         
10    Japan_INS SENSOR        2020-07-01  Japan       
11    Americas_CHECKER        2020-07-01  Americas    
12    KIA_PC VISION           2020-07-01  KIA         
13    GTR China_DEEP LEARNING 2020-07-01  GTR China   
14    GTR China_ID MOBILE     2020-07-01  GTR China   
15    KIA_CHECKER             2020-07-01  KIA         
16    GTR China_INS FACTRY    2020-07-01  GTR China   
17    GTR China_INS SENSOR    2020-07-01  GTR China   
18    Americas_PC VISION      2020-07-01  Americas    
19    KIA_3D SENSOR           2020-07-01  KIA         
20    GTR China_3D            2020-07-01  GTR China   
21    Americas_INS SENSOR     2020-07-01  Americas    
22    Europe_WAFER ID         2020-07-01  Europe      
23    KIA_ID MOBILE           2020-07-01  KIA         
24    Europe_CHECKER          2020-07-01  Europe      
25    Europe_DATAMAN          2020-07-01  Europe      
26    Europe_DEEP LEARNING    2020-07-01  Europe      
27    Europe_3D SENSOR        2020-07-01  Europe      
28    KIA_Other               2020-07-01  KIA         
29    Europe_ID MOBILE        2020-07-01  Europe      
30    KIA_INSIGHT ID          2020-07-01  KIA         
31    Europe_INS FACTRY       2020-07-01  Europe      
32    Europe_INS SENSOR       2020-07-01  Europe      
33    Europe_INSIGHT ID       2020-07-01  Europe      
34    Americas_ID MOBILE      2020-07-01  Americas    
35    Americas_DEEP LEARNING  2020-07-01  Americas    
36    KIA_INS SENSOR          2020-07-01  KIA         
37    Europe_Other            2020-07-01  Europe      
38    Europe_3D               2020-07-01  Europe      
39    KIA_INS FACTRY          2020-07-01  KIA         
40    Europe_PC VISION        2020-07-01  Europe      
41    GTR China_INSIGHT ID    2020-07-01  GTR China   
42    KIA_DATAMAN             2020-07-01  KIA         
43    Americas_Other          2020-07-01  Americas    
44    Japan_ID MOBILE         2020-07-01  Japan       
45    GTR China_PC VISION     2020-07-01  GTR China   
46    GTR China_WAFER ID      2020-07-01  GTR China   
47    Japan_DEEP LEARNING     2020-07-01  Japan       
48    Japan_PC VISION         2020-07-01  Japan       
49    Japan_WAFER ID          2020-07-01  Japan       
50    Japan_DATAMAN           2020-07-01  Japan       
51    Americas_ADV ENGINE     2020-07-01  Americas    
52    Americas_INSIGHT ID     2020-07-01  Americas    
53    Americas_3D SENSOR      2020-07-01  Americas    
54    Japan_INSIGHT ID        2020-07-01  Japan       
55    KIA_3D                  2020-07-01  KIA         
56    GTR China_Other         2020-07-01  GTR China   
57    Americas_INS FACTRY     2020-07-01  Americas    
58    Japan_3D SENSOR         2020-07-01  Japan       
59    Japan_3D                2020-07-01  Japan       
60    Japan_INS FACTRY        2020-07-01  Japan       
61    Japan_Other             2020-07-01  Japan       
62    Japan_ADV ENGINE        2020-07-01  Japan       
63    Americas_DEEP LEARNING  2020-06-01  Americas    
64    Americas_CHECKER        2020-06-01  Americas    
65    Americas_ADV ENGINE     2020-06-01  Americas    
66    KIA_INS SENSOR          2020-06-01  KIA         
67    Japan_Other             2020-06-01  Japan       
68    Europe_3D               2020-06-01  Europe      
69    Americas_3D SENSOR      2020-06-01  Americas    
70    KIA_INS FACTRY          2020-06-01  KIA         
71    Europe_Other            2020-06-01  Europe      
72

In [56]:
final_df.sort_values(by=[ts_settings['series_id'],ts_settings['date_col']], inplace=True)

In [57]:
final_df.head()

Area_product month_date  Area_Txt  \
2047  Americas_3D 2017-12-01  Americas   
1999  Americas_3D 2018-01-01  Americas   
1924  Americas_3D 2018-02-01  Americas   
1831  Americas_3D 2018-03-01  Americas   
1779  Americas_3D 2018-04-01  Americas   

                                                                                 region_Txt  \
2047  Americas East, Other, Americas West, Americas Central, Americas LATAM, Americas South   
1999  Americas East, Other, Americas West, Americas Central, Americas LATAM, Americas South   
1924  Americas East, Other, Americas West, Americas Central, Americas LATAM, Americas South   
1831  Americas East, Other, Americas West, Americas Central, Americas LATAM, Americas South   
1779  Americas East, Other, Americas West, Americas Central, Americas LATAM, Americas South   

                                                 industry1_Txt  \
2047  Electronics, Automotive, Other, Packaging                  
1999  Electronics, Automotive, Other, Packaging                  
1924  Electronics, Semiconductor, Packaging, Automotive, Other   
1831  Electronics, Semiconductor, Packaging, Automotive, Other   
1779  Electronics, Semiconductor, Packaging, Automotive, Other   

                                                           account_class_Txt  \
2047  Strategic, Non-Strategic, Strategic Existing, White Space                
1999  Strategic, Most Wanted, Non-Strategic, White Space, Strategic Existing   
1924  Strategic, Most Wanted, Non-Strategic, White Space, Strategic Existing   
1831  Strategic, Most Wanted, Non-Strategic, White Space, Strategic Existing   
1779  Strategic, Non-Strategic, Strategic Existing, White Space                

     product_Txt  Area_nunique  region_nunique  industry1_nunique  \
2047  3D          1.0           6.0             4.0                 
1999  3D          1.0           6.0             4.0                 
1924  3D          1.0           6.0             5.0                 
1831  3D          1.0           6.0             5.0                 
1779  3D          1.0           6.0             5.0                 

      account classification_nunique  product_nunique  booking value  \
2047  4.0                             1.0              801699.0        
1999  5.0                             1.0              184511.0        
1924  5.0                             1.0              49768.0         
1831  5.0                             1.0              733159.0        
1779  4.0                             1.0              655603.0        

      nb of appointments_sum  nb of technical request_sum  \
2047  0.0                     0.0                           
1999  0.0                     25.0                          
1924  0.0                     79.0                          
1831  0.0                     150.0                         
1779  0.0                     130.0                         

      nb of opportunities created_sum  nb of opportunities forecasted_sum  \
2047  42.0                             0.0                                  
1999  0.0                              0.0                                  
1924  0.0                              0.0                                  
1831  0.0                              0.0                                  
1779  0.0                              0.0                                  

      nb of opportunities qualified_sum  weighed funnel values_sum  \
2047  42.0                               0.0                         
1999  55.0                               0.0                         
1924  70.0                               0.0                         
1831  72.0                               0.0                         
1779  59.0                               0.0                         

      opportunities average nb of months_sum  
2047  0.0                                     
1999  0.0                                     
1924  0.0                                     
1831  0.0       

In [58]:
final_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2070 entries, 2047 to 0
Data columns (total 20 columns):
 #   Column                                  Non-Null Count  Dtype         
---  ------                                  --------------  -----         
 0   Area_product                            2070 non-null   object        
 1   month_date                              2070 non-null   datetime64[ns]
 2   Area_Txt                                1969 non-null   object        
 3   region_Txt                              1969 non-null   object        
 4   industry1_Txt                           1969 non-null   object        
 5   account_class_Txt                       1969 non-null   object        
 6   product_Txt                             1969 non-null   object        
 7   Area_nunique                            2070 non-null   float64       
 8   region_nunique                          2070 non-null   float64       
 9   industry1_nunique                       2070 non-nul

In [74]:
final_df['date1']= pd.to_datetime(final_df['month_date'].dt.strftime("%Y-%m"))

In [75]:
#Set all values here.
#One important point, if you decide to change to monthly or weekly ts_settings should be 
#Changed afterwards, as weekly and monthly dates are based on the original date_col

today = pd.to_datetime("today")
target = 'booking value'
date_col = 'date1'
kia = ['nb of opportunities forecasted', 'weighed funnel values', 'opportunities average nb of months']
series_id = 'Area_product'
pj_name = series_id + "_Project"+"_"+str(today)[0:10]
fd_start = 1
fd_end = 1
fdw_start = -3
fdw_end = 0
num_backtests = 2
#calendar =dr.CalendarFile.create("canada_calendar.csv")
# Create TS Settings
ts_settings = {'use_time_series':training,'project_name':pj_name, 'known_in_advance':kia,
               'series_id':series_id,  'target':target, 'date_col':date_col,'num_backtests':num_backtests,
               'fd_start':fd_start, 'fd_end':fd_end, 'fdw_start':fdw_start, 'fdw_end':fdw_end
               }



In [76]:
# Rerun our data quality check
ts_describe = dr_helpers.DataQualityCheck(final_df, ts_settings)

Running all data quality checks...

There are 2070 rows and 21 columns
There are 70 series
The data spans from  2017-12-01 00:00:00 to 2020-07-01 00:00:00
Data fails hierarchical check! No hierarchical blueprints will run.
Minimum target value is <> 0. Zero-inflated blueprints will not run.
 16.00% of the series appeared after the start of the training data
 9.00% of the series were removed before the end of the training data
No duplicate timestamps detected within any series
0.00% of series have at least one missing time step.
0.00% of the rows are missing a target value
11.43% series have zeros in more than 99.00% or more of the rows


ValueError: 2678400.0 seconds is not a supported timestep

In [81]:
final_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2070 entries, 2047 to 0
Data columns (total 21 columns):
 #   Column                                  Non-Null Count  Dtype         
---  ------                                  --------------  -----         
 0   Area_product                            2070 non-null   object        
 1   month_date                              2070 non-null   datetime64[ns]
 2   Area_Txt                                1969 non-null   object        
 3   region_Txt                              1969 non-null   object        
 4   industry1_Txt                           1969 non-null   object        
 5   account_class_Txt                       1969 non-null   object        
 6   product_Txt                             1969 non-null   object        
 7   Area_nunique                            2070 non-null   float64       
 8   region_nunique                          2070 non-null   float64       
 9   industry1_nunique                       2070 non-nul

In [82]:
final_df.head()

Area_product month_date  Area_Txt  \
2047  Americas_3D         2017-12-01  Americas   
2066  Americas_3D SENSOR  2017-12-01  Americas   
2069  Americas_ADV ENGINE 2017-12-01  Americas   
2021  Americas_CHECKER    2017-12-01  Americas   
2013  Americas_DATAMAN    2017-12-01  Americas   

                                                                                 region_Txt  \
2047  Americas East, Other, Americas West, Americas Central, Americas LATAM, Americas South   
2066  Americas East, Other, Americas West, Americas Central, Americas LATAM, Americas South   
2069  Americas East                                                                           
2021  Americas East, Americas West, Americas Central, Americas LATAM, Americas South          
2013  Americas East, Other, Americas West, Americas Central, Americas LATAM, Americas South   

                                                            industry1_Txt  \
2047  Electronics, Automotive, Other, Packaging                             
2066  Electronics, Automotive, Other, Packaging                             
2069  Other                                                                 
2021  Electronics, Automotive, Other, Packaging                             
2013  Electronics, Semiconductor, Packaging, Automotive, Other, Logistics   

                                                                  account_class_Txt  \
2047  Strategic, Non-Strategic, Strategic Existing, White Space                       
2066  Strategic, Most Wanted, Non-Strategic, White Space, Strategic Existing          
2069  Strategic Existing                                                              
2021  Strategic, Non-Strategic, Strategic Existing, White Space                       
2013  Strategic, Other, Most Wanted, Non-Strategic, White Space, Strategic Existing   

     product_Txt  Area_nunique  region_nunique  industry1_nunique  ...  \
2047  3D          1.0           6.0             4.0                ...   
2066  3D SENSOR   1.0           6.0             4.0                ...   
2069  ADV ENGINE  1.0           1.0             1.0                ...   
2021  CHECKER     1.0           5.0             4.0                ...   
2013  DATAMAN     1.0           6.0             6.0                ...   

      product_nunique  booking value  nb of appointments_sum  \
2047  1.0              801699.0       0.0                      
2066  1.0              107650.0       0.0                      
2069  1.0              0.0            0.0                      
2021  1.0              128613.0       0.0                      
2013  1.0              4831862.0      0.0                      

      nb of technical request_sum  nb of opportunities created_sum  \
2047  0.0                          42.0                              
2066  0.0                          35.0                              
2069  0.0                          2.0                               
2021  0.0                          7.0                               
2013  0.0                          418.0                             

      nb of opportunities forecasted_sum  nb of opportunities qualified_sum  \
2047  0.0                                 42.0                                
2066  0.0                                 34.0                                
2069  0.0                                 2.0                                 
2021  0.0                                 6.0                                 
2013  0.0                                 400.0                               

      weighed funnel values_sum  opportunities average nb of months_sum  \
2047  0.0                        0.0                                      
2066  0.0                        0.0                                      
2069  0.0                        0.0                                      
2021  0.0                        0.0                                      
2013  0.0                        0.0                  

In [79]:
ts_settings["series_id"]

'Area_product'

In [80]:
ts_settings["date_col"]

'date1'

In [77]:
deltas = final_df.groupby(ts_settings["series_id"])[ts_settings["date_col"]].diff().reset_index(drop=True)

In [78]:
deltas.head()

0   NaT
1   NaT
2   NaT
3   NaT
4   NaT
Name: date1, dtype: timedelta64[ns]

In [ ]:
median_timestep = deltas.apply(lambda x: x.total_seconds()).median()

In [61]:
final_df.head()

Area_product month_date  Area_Txt  \
2047  Americas_3D 2017-12-01  Americas   
1999  Americas_3D 2018-01-01  Americas   
1924  Americas_3D 2018-02-01  Americas   
1831  Americas_3D 2018-03-01  Americas   
1779  Americas_3D 2018-04-01  Americas   

                                                                                 region_Txt  \
2047  Americas East, Other, Americas West, Americas Central, Americas LATAM, Americas South   
1999  Americas East, Other, Americas West, Americas Central, Americas LATAM, Americas South   
1924  Americas East, Other, Americas West, Americas Central, Americas LATAM, Americas South   
1831  Americas East, Other, Americas West, Americas Central, Americas LATAM, Americas South   
1779  Americas East, Other, Americas West, Americas Central, Americas LATAM, Americas South   

                                                 industry1_Txt  \
2047  Electronics, Automotive, Other, Packaging                  
1999  Electronics, Automotive, Other, Packaging                  
1924  Electronics, Semiconductor, Packaging, Automotive, Other   
1831  Electronics, Semiconductor, Packaging, Automotive, Other   
1779  Electronics, Semiconductor, Packaging, Automotive, Other   

                                                           account_class_Txt  \
2047  Strategic, Non-Strategic, Strategic Existing, White Space                
1999  Strategic, Most Wanted, Non-Strategic, White Space, Strategic Existing   
1924  Strategic, Most Wanted, Non-Strategic, White Space, Strategic Existing   
1831  Strategic, Most Wanted, Non-Strategic, White Space, Strategic Existing   
1779  Strategic, Non-Strategic, Strategic Existing, White Space                

     product_Txt  Area_nunique  region_nunique  industry1_nunique  ...  \
2047  3D          1.0           6.0             4.0                ...   
1999  3D          1.0           6.0             4.0                ...   
1924  3D          1.0           6.0             5.0                ...   
1831  3D          1.0           6.0             5.0                ...   
1779  3D          1.0           6.0             5.0                ...   

      product_nunique  booking value  nb of appointments_sum  \
2047  1.0              801699.0       0.0                      
1999  1.0              184511.0       0.0                      
1924  1.0              49768.0        0.0                      
1831  1.0              733159.0       0.0                      
1779  1.0              655603.0       0.0                      

      nb of technical request_sum  nb of opportunities created_sum  \
2047  0.0                          42.0                              
1999  25.0                         0.0                               
1924  79.0                         0.0                               
1831  150.0                        0.0                               
1779  130.0                        0.0                               

      nb of opportunities forecasted_sum  nb of opportunities qualified_sum  \
2047  0.0                                 42.0                                
1999  0.0                                 55.0                                
1924  0.0                                 70.0                                
1831  0.0                                 72.0                                
1779  0.0                                 59.0                                

      weighed funnel values_sum  opportunities average nb of months_sum  \
2047  0.0                        0.0                                      
1999  0.0                        0.0                                      
1924  0.0                        0.0                                      
1831  0.0                        0.0                                      
1779  0.0                        0.0                                      

        date1  
2047  2017-12  
1999  2018-01  
1924  2018-02  
1831  2018-03  
1779  2018-04  

[5 rows x 21 columns]

In [103]:
#Decide which one to save, and then just change the name
final_df.to_csv(ts_settings['project_name']+'monthkia'+".csv")

In [33]:
final_df.columns

Index(['Area_product', 'month_date', 'Area_Txt', 'region_Txt', 'industry1_Txt',
       'account_class_Txt', 'product_Txt', 'Area_nunique', 'region_nunique',
       'industry1_nunique', 'account classification_nunique',
       'product_nunique', 'booking value', 'nb of appointments_sum',
       'nb of technical request_sum', 'nb of opportunities created_sum',
       'nb of opportunities forecasted_sum',
       'nb of opportunities qualified_sum', 'weighed funnel values_sum',
       'opportunities average nb of months_sum'],
      dtype='object')

In [104]:
def start_modeling():
    '''provide a project name, and the dataframe for training
        1. Create project
        2. Set specifications for time-series modeling
        3. Start project'''
    project = dr.Project.create(project_name=ts_settings['project_name'], sourcedata=ts_settings['use_time_series'])
    mySpec = dr.DatetimePartitioningSpecification(
                datetime_partition_column=ts_settings['date_col'],
                use_time_series=True,
                multiseries_id_columns=[ts_settings['series_id']],
                number_of_backtests = ts_settings['num_backtests'],
                default_to_known_in_advance=False,
                feature_derivation_window_start=ts_settings['fdw_start'],
                feature_derivation_window_end= ts_settings['fdw_end'],
                forecast_window_start=ts_settings['fd_start'],
                forecast_window_end=ts_settings['fd_end'],
        

    )
    project.set_target(
            target = ts_settings['target'],
            partitioning_method = mySpec,
            max_wait = 1000000,
            mode=dr.AUTOPILOT_MODE.QUICK  ##### Here is where we can change to dr.AUTOPILOT_MODE.FULL_AUTO
    )
    project.wait_for_autopilot()  ##Wait for autopilot to finish
    return(project)

In [105]:
#You can add a calendar as follows
project = start_modeling()

In progress: 2, queued: 11 (waited: 0s)
In progress: 2, queued: 11 (waited: 1s)
In progress: 2, queued: 11 (waited: 2s)
In progress: 2, queued: 11 (waited: 3s)
In progress: 2, queued: 11 (waited: 4s)
In progress: 2, queued: 11 (waited: 7s)
In progress: 2, queued: 11 (waited: 11s)
In progress: 2, queued: 11 (waited: 18s)
In progress: 2, queued: 11 (waited: 31s)
In progress: 2, queued: 11 (waited: 52s)
In progress: 2, queued: 9 (waited: 73s)
In progress: 2, queued: 9 (waited: 93s)
In progress: 2, queued: 9 (waited: 114s)
In progress: 2, queued: 8 (waited: 135s)
In progress: 2, queued: 7 (waited: 155s)
In progress: 2, queued: 7 (waited: 176s)
In progress: 2, queued: 6 (waited: 197s)
In progress: 2, queued: 5 (waited: 217s)
In progress: 6, queued: 0 (waited: 238s)
In progress: 6, queued: 0 (waited: 259s)
In progress: 5, queued: 0 (waited: 279s)
In progress: 1, queued: 0 (waited: 300s)
In progress: 4, queued: 0 (waited: 320s)
In progress: 4, queued: 0 (waited: 341s)
In progress: 1, queued: 

### Data quality check

In [57]:
# Rerun our data quality check
ts_describe = data_quality_check(final_df, ts_settings)

Running all data quality checks...

There are 2070 rows and 20 columns
There are 70 series
The data spans from  2017-12-01 00:00:00 to 2020-07-01 00:00:00
Data fails hierarchical check! No hierarchical blueprints will run.
Minimum target value is > 0. Zero-inflated blueprints will not run.
 16.00% of the series appeared after the start of the training data
 9.00% of the series were removed before the end of the training data
No duplicate timestamps detected within any series
No leading or trailing zeros detected within series
0.00% of series have at least one missing time step.
0.00% of the rows are missing a target value
11.43% series have zeros in more than 99.00% or more of the rows


ValueError: 2678400.0 seconds is not a supported timestep

In [58]:
training = fill_missing_dates(final_df, ts_settings)

ValueError: 2678400.0 seconds is not a supported timestep

### Plot series

In [59]:
# Plot our average target over time
plot_series_average(final_df, ts_settings)

In [60]:
# Bottom 35 series
plot_individual_series(final_df, ts_settings, n=35, top=False)

In [61]:
# Top 35 series
plot_individual_series(final_df, ts_settings, n=35, top=True)

In [62]:
# Create and plot a Holiday calendar
plot_ts_calendar(final_df, ts_settings, calendar=None)

#Note: you don't need to have an already created calendar

ValueError: 2678400.0 seconds is not a supported timestep

### Clustering

In [67]:
# Series clustering
method='correlation'
nlags=None
alpha=None
scale=True
scale_method=None
split_method=None
n_clusters=None
max_clusters= 2
plot=True

df_w_clusters =  add_cluster_labels(final_df, 
                                    ts_settings, 
                                    method=method,
                                    scale=scale,
                                    scale_method=scale_method,
                                    alpha=alpha,
                                    nlags=nlags, 
                                    split_method=split_method,
                                    n_clusters=n_clusters, 
                                    max_clusters=max_clusters, 
                                    plot=True)

plot_clusters(df_w_clusters, ts_settings)

Testing 2 to 2 clusters
For n_clusters = 2, silhouette score is 0.26787188484505303
optimal n_clusters = 2, max silhouette score is 0.26787188484505303


In [64]:
# We can force 4 clusters
method='correlation'
nlags=None
alpha=None
scale=True
scale_method=None
n_clusters=4
max_clusters=None
plot=True

df_w_clusters =  add_cluster_labels(final_df, 
                                    ts_settings, 
                                    method=method,
                                    scale=scale,
                                    scale_method=scale_method,
                                    alpha=alpha,
                                    nlags=nlags, 
                                    n_clusters=n_clusters, 
                                    max_clusters=max_clusters, 
                                    plot=True)

plot_clusters(df_w_clusters, ts_settings)

### Add cross series features

In [69]:
df_w_clusters.head(3)

Area_product month_date  Area_Txt  \
0   Americas_3D         2017-12-01  Americas   
32  Americas_3D SENSOR  2017-12-01  Americas   
64  Americas_ADV ENGINE 2017-12-01  Americas   

                                                                               region_Txt  \
0   Americas LATAM, Other, Americas East, Americas West, Americas Central, Americas South   
32  Americas LATAM, Other, Americas East, Americas West, Americas Central, Americas South   
64  Americas East                                                                           

                                industry1_Txt  \
0   Other, Electronics, Automotive, Packaging   
32  Other, Electronics, Automotive, Packaging   
64  Other                                       

                                                         account_class_Txt  \
0   Strategic, White Space, Strategic Existing, Non-Strategic                
32  Strategic Existing, Non-Strategic, Strategic, Most Wanted, White Space   
64  Strategic Existing                                                       

   product_Txt  Area_nunique  region_nunique  industry1_nunique  ...  \
0   3D          1.0           6.0             4.0                ...   
32  3D SENSOR   1.0           6.0             4.0                ...   
64  ADV ENGINE  1.0           1.0             1.0                ...   

    product_nunique  booking value  nb of appointments_sum  \
0   1.0              801699.0       0.0                      
32  1.0              107650.0       0.0                      
64  1.0              0.0            0.0                      

    nb of technical request_sum  nb of opportunities created_sum  \
0   0.0                          42.0                              
32  0.0                          35.0                              
64  0.0                          2.0                               

    nb of opportunities forecasted_sum  nb of opportunities qualified_sum  \
0   0.0                                 42.0                                
32  0.0                                 34.0                                
64  0.0                                 2.0                                 

    weighed funnel values_sum  opportunities average nb of months_sum  Cluster  
0   0.0                        0.0                                     0        
32  0.0                        0.0                                     0        
64  0.0                        0.0                                     0        

[3 rows x 21 columns]

In [71]:
df_w_clusters.columns

Index(['Area_product', 'month_date', 'Area_Txt', 'region_Txt', 'industry1_Txt',
       'account_class_Txt', 'product_Txt', 'Area_nunique', 'region_nunique',
       'industry1_nunique', 'account classification_nunique',
       'product_nunique', 'booking value', 'nb of appointments_sum',
       'nb of technical request_sum', 'nb of opportunities created_sum',
       'nb of opportunities forecasted_sum',
       'nb of opportunities qualified_sum', 'weighed funnel values_sum',
       'opportunities average nb of months_sum', 'Cluster'],
      dtype='object')

In [72]:
#Set all values here.
#One important point, if you decide to change to monthly or weekly ts_settings should be 
#Changed afterwards, as weekly and monthly dates are based on the original date_col

today = pd.to_datetime("today")
target = 'booking value'
date_col = 'month_date'
kia = ['nb of opportunities forecasted_sum', 'weighed funnel values_sum', 'opportunities average nb of months_sum']
series_id = 'Area_product'
pj_name = series_id + "_Project"+"_"+str(today)[0:10]
fd_start = 1
fd_end = 1
fdw_start = -3
fdw_end = 0
num_backtests = 2
#calendar =dr.CalendarFile.create("canada_calendar.csv")
# Create TS Settings
ts_settings = {'use_time_series':training,'project_name':pj_name, 'known_in_advance':kia,
               'series_id':series_id,  'target':target, 'date_col':date_col,'num_backtests':num_backtests,
               'fd_start':fd_start, 'fd_end':fd_end, 'fdw_start':fdw_start, 'fdw_end':fdw_end
               }

In [84]:
# Set defaults

target = 'booking value'
date_col = 'month_date'
series_id = 'Area_product'
kia = ['nb of opportunities forecasted_sum', 'weighed funnel values_sum', 'opportunities average nb of months_sum']
num_backtests = 3
validation_duration = 1
holdout_duration = 1
disable_holdout = True
metric = 'RMSE'
use_time_series=True
fd_start = 1
fd_end = 1
fdw_start = -3
fdw_end = 0
max_date = pd.to_datetime(training[date_col]).max()

# Create TS Settings
ts_settings = {'max_date':max_date, 'known_in_advance':kia, 'num_backtests':num_backtests, 
               'validation_duration':validation_duration, 'holdout_duration':holdout_duration,
               'disable_holdout':disable_holdout,'use_time_series':use_time_series,
               'series_id':series_id, 'metric':metric, 'target':target, 'date_col':date_col,
               'fd_start':fd_start, 'fd_end':fd_end, 'fdw_start':fdw_start, 'fdw_end':fdw_end}

In [73]:
df_w_clusters =  create_cross_series_features(df_w_clusters, 
                                              group=[date_col,'Cluster'], 
                                              cols=[target,'nb of opportunities created_sum','nb of opportunities qualified_sum'], 
                                              funcs=['mean','std'])
df_w_clusters.head(2)

Area_product month_date  Area_Txt  \
0  Americas_3D        2017-12-01  Americas   
1  Americas_3D SENSOR 2017-12-01  Americas   

                                                                              region_Txt  \
0  Americas LATAM, Other, Americas East, Americas West, Americas Central, Americas South   
1  Americas LATAM, Other, Americas East, Americas West, Americas Central, Americas South   

                               industry1_Txt  \
0  Other, Electronics, Automotive, Packaging   
1  Other, Electronics, Automotive, Packaging   

                                                        account_class_Txt  \
0  Strategic, White Space, Strategic Existing, Non-Strategic                
1  Strategic Existing, Non-Strategic, Strategic, Most Wanted, White Space   

  product_Txt  Area_nunique  region_nunique  industry1_nunique  ...  \
0  3D          1.0           6.0             4.0                ...   
1  3D SENSOR   1.0           6.0             4.0                ...   

   nb of opportunities qualified_sum  weighed funnel values_sum  \
0  42.0                               0.0                         
1  34.0                               0.0                         

   opportunities average nb of months_sum  Cluster  booking value_mean  \
0  0.0                                     0        1.097396e+06         
1  0.0                                     0        1.097396e+06         

   booking value_std  nb of opportunities created_sum_mean  \
0  2.112247e+06       100.428571                             
1  2.112247e+06       100.428571                             

   nb of opportunities created_sum_std  \
0  156.379642                            
1  156.379642                            

   nb of opportunities qualified_sum_mean  \
0  98.190476                                
1  98.190476                                

   nb of opportunities qualified_sum_std  
0  154.146151                             
1  154.146151                             

[2 rows x 27 columns]

In [88]:
# Build separate projects by forecast distance, feature derivation window, and/or cluster
fdws=[(-5,0),(-3,0),(-2,0)]
fds = [(1,1)]

In [89]:
projects = create_dr_projects(df_w_clusters, 
                             ts_settings, 
                             prefix='TS',
                             split_col='Cluster', 
                             fdws=fdws, 
                             fds=fds)

Kicking off 6 projects

Building Next Project 
...



ValueError: 2678400.0 seconds is not a supported timestep